In [1]:
#Dimitris Spathis {dispathis@gmail.com} Nov 2016
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
#%pylab inline
import mpld3
mpld3.enable_notebook()

In [2]:
data = pd.read_csv('generated-author-info.csv')

In [3]:
countries = pd.read_csv('country-info.csv')
countries = countries[countries.region.str.contains("europe") == True]

In [4]:
pattern = '|'.join(countries.institution)
data["europe"] = data.dept.str.contains(pattern)

In [5]:
# 'mlmining' : ['NIPS', 'ICML','KDD']
# 'ai' : ['AAAI', 'AAAI/IAAI', 'IJCAI']
#  'ir' : ['WWW', 'SIGIR']
# 'chi' : ['CHI','UbiComp','Ubicomp','UIST']
# 'nlp' : ['EMNLP','ACL','ACL (1)', 'ACL (2)', 'NAACL', 'HLT-NAACL'] 
# 'vision' : ['CVPR', 'CVPR (1,2,3...), ICCV', 'ECCV (1,2,3...)']

# you can choose your fields here 
# https://github.com/emeryberger/CSrankings/blob/cec0143fbe6cbdbcd6c83f640ac24f665580307b/util/csrankings.py#L55

data = (data.loc[data['area'].isin(['mlmining', 'chi', 'ir', 'nlp', 'ai'])])

In [6]:
# Adjusted counts: each publication is counted exactly once, with credit adjusted by splitting evenly
# across all co-authors. This approach makes it impossible to boost rankings simply by adding authors to a paper.

aggregations = {
    
    'adjustedcount':  'sum',
    'year':  np.mean,
    'count' : 'sum', 
    'europe': 'unique',
    'area': {
        'publications': 'count',
        'fields': 'unique'
    }
}

In [7]:
grouped = data.groupby(['name', 'dept']).agg(aggregations)

In [8]:
#display dataframe in full length
pd.set_option('display.max_rows', None)

In [9]:
df = grouped.sort([('adjustedcount', 'sum')], ascending=False)

/home/sdimi/anaconda3/envs/py27/lib/python2.7/site-packages/ipykernel/__main__.py:1: FutureWarning: sort(columns=....) is deprecated, use sort_values(by=.....)
  if __name__ == '__main__':


In [10]:
#transform categorical [nlp, ai, mlmining, ir] => columns nlp 1 | ai 1 | chi 0 ...etc
df = pd.concat([df, df[('area', 'fields')].str.join(sep=',').str.get_dummies(sep=',')], axis=1)

In [11]:
#arbitrary weights based on your preferences, will be used for scatter size
df["weight"] = df.ai*2 + df.chi*9 +df.ir*2 + df.mlmining*9 + df.nlp*7 

In [12]:
df

(count, sum)  \
name                             dept                                                       
Michael I. Jordan                University of California - Berkeley                138.0   
Dan Roth                         University of Illinois at Urbana-Champaign          99.0   
Craig Boutilier                  University of Toronto                               72.0   
Christopher D. Manning           Stanford University                                100.0   
Dan Klein                        University of California - Berkeley                 89.0   
Tuomas Sandholm                  Carnegie Mellon University                          77.0   
Pedro M. Domingos                University of Washington                            61.0   
Richard E. Korf                  University of California - Los Angeles              47.0   
Raymond J. Mooney                University of Texas at Austin                       67.0   
Jieping Ye                       University of Michigan                             101.0   
Satinder P. Singh                University of Michigan                              75.0   
W. Bruce Croft                   University of Massachusetts Amherst                 60.0   
Eric P. Xing                     Carnegie Mellon University                          91.0   
Ravin Balakrishnan               University of Toronto                               81.0   
William W. Cohen                 Carnegie Mellon University                          57.0   
Andrew McCallum                  University of Massachusetts Amherst                 73.0   
Yoshua Bengio                    University of Montreal                              85.0   
Bernhard Schölkopf               Max Planck Institute                                92.0   
Toby Walsh                       UNSW                                                68.0   
Vincent Ng                       University of Texas at Dallas                       47.0   
Vincent Conitzer                 Duke University                                     61.0   
Mirella Lapata                   University of Edinburgh                             54.0   
Hal Daumé III                    University of Maryland - College Park               63.0   
Daphne Koller                    Stanford University                                 72.0   
Hwee Tou Ng                      National University of Singapore                    60.0   
Andrew W. Moore 0001             Carnegie Mellon University                          56.0   
Thorsten Joachims                Cornell University                                  47.0   
Daniel S. Weld                   University of Washington                            64.0   
Noah A. Smith                    University of Washington                            71.0   
Jiawei Han                       University of Illinois at Urbana-Champaign          97.0   
Eugene Charniak                  Brown University                                    43.0   
Bing Liu 0001                    University of Illinois at Chicago                   60.0   
ChengXiang Zhai                  University of Illinois at Urbana-Champaign          60.0   
Regina Barzilay                  Massachusetts Institute of Technology               62.0   
Peter Stone                      University of Texas at Austin                       52.0   
Kevin Knight                     University of Southern California                   58.0   
Philip S. Yu                     University of Illinois at Chicago                   76.0   
Hector J. Levesque               University of Toronto                               40.0   
Francis R. Bach                  Ecole Normale Superieure                            47.0   
Thomas G. Dietterich             Oregon State University                             49.0   
Padhraic Smyth                   University of California - Irvine                   48.0   
Michael L. Littman               Brown University                             

In [13]:
counts = []
years = []
names = []
weights = []
countries = []
for i in range(df.shape[0]):
    counts.append((df[('adjustedcount', 'sum')][i]))
    years.append((df[('year', 'mean')][i]))
    names.append((list(df.index.values))[i])
    countries.append(df[('europe', 'unique')][i])
    weights.append((df['weight'][i]))

In [14]:
counts = np.array(counts)
years = np.array(years)
weights = np.array(weights)
countries = np.array(countries)
#names = np.array(names)

In [15]:
%matplotlib inline
import matplotlib.pyplot as plt
fig, ax = plt.subplots(figsize=(12,8))


custom_colors = ['red' if countries[i] == True else 'blue' for i in range(df.shape[0])]
scatter = ax.scatter(years,counts, c=custom_colors, s=weights*10, alpha=0.2)

ax.set_title("Computer Science professors in ML/AI/HCI/NLP by their avg. publication time in top venues", fontsize=15)
ax.set_ylabel('Adjusted publication count', fontsize=15)
ax.set_xlabel('Avg year of their publications', fontsize=15)
ax.grid(color='lightgray', alpha=0.7)

plt.locator_params(nbins=25)
labels = names
tooltip = mpld3.plugins.PointLabelTooltip(scatter, labels=labels, location='mouse')
mpld3.plugins.connect(fig, tooltip)

mpld3.save_html(fig, 'interactive_figure.html')
mpld3.display(fig)